In [14]:
import numpy as np
import pandas as pd
import os
import csv
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
import seaborn as sns
import subprocess

In [59]:
def read_namelist(relative_path):
    """
    Read a Fortran namelist file and extract parameters from a relative path.

    Parameters:
    relative_path (str): Relative path to the namelist file from the notebook.

    Returns:
    dict: Dictionary of parameters read from the file.
    """
    # Construct the full path using the notebook's directory
    notebook_dir = os.getcwd()  # Gets the directory of the current script
    file_path = os.path.join(notebook_dir, relative_path)  # Constructs the full path

    params = {}
    try:
        with open(file_path, 'r') as file:
            for line in file:
                line = line.strip()
                if line.startswith('&') or line.startswith('/'):
                    continue
                key_value = line.split('=')
                if len(key_value) == 2:
                    key = key_value[0].strip()
                    value = key_value[1].strip().rstrip('/')
                    # Convert numerical values from strings
                    if value.isdigit():
                        value = int(value)
                    else:
                        try:
                            value = float(value)
                        except ValueError:
                            pass  # Keep as string if it's not a number
                    params[key] = value
    except FileNotFoundError:
        print(f"Error: The file '{file_path}' does not exist.")
    except Exception as e:
        print(f"An unexpected error occurred: {e}")

    return params

# Example usage
relative_path = '../../data/namelist/ex_5.nml'
parameters = read_namelist(relative_path)
print(parameters)
nx = parameters['nx']
ny = parameters['ny']

{'nx': 16, 'ny': 16, 'kappa': 1.0, 'total_time': 10.0, 'a_adv': 0.03, 'a_diff': 0.03, 'B': 10.0, 'init_State': "'rand'"}


In [7]:

def read_and_reshape_temperature_csv(file_name, nx, ny):
    """
    Read temperature data from a CSV file, using the first row for matrix dimensions,
    and reshape subsequent rows into matrices using these dimensions.
    """
    # Calculate the correct relative path to the data directory
    notebook_path = os.getcwd()  # Gets the current working directory where the notebook is running
    data_path = os.path.join(notebook_path, '../../data', file_name)  # Moves up two directories and then to 'data'

    with open(data_path, 'r') as file:
        reader = csv.reader(file, delimiter=',', skipinitialspace=True)

        # Prepare to collect all data
        all_data = []

        for row in reader:
            # Convert each row to floats and collect data
            float_row = [float(num) for num in row]
            all_data.extend(float_row)

    # Now, reshape the data into the desired format
    if len(all_data) % (nx * ny) != 0:
        raise ValueError("Data size does not match expected dimensions.")

    all_data = np.array(all_data)
    matrix = all_data.reshape(-1, nx, ny)

    return matrix






(102, 8, 8)

In [33]:
def plot_heatmap_animation(matrices, title='Heatmap Animation', xlabel='X-axis', ylabel='Y-axis', interval=500):
    """
    Create an animated heatmap from a list of matrices, with a consistent color bar.

    Parameters:
    matrices (list of np.ndarray): List of matrices to animate.
    title (str): Title of the animation.
    xlabel (str): Label for the x-axis.
    ylabel (str): Label for the y-axis.
    interval (int): Time interval between frames in milliseconds.
    """
    # Ensure all matrices are numpy arrays
    matrices = [np.array(matrix) if not isinstance(matrix, np.ndarray) else matrix for matrix in matrices]

    fig, ax = plt.subplots(figsize=(10, 8))
    cbar_ax = fig.add_axes([.91, .3, .03, .4])  # Adjust these to fit the layout and size of your figure

    # Start by displaying the first matrix and setting up the color bar
    sns.heatmap(matrices[0], annot=True, fmt=".2f", cmap='viridis', cbar=True, ax=ax, cbar_ax=cbar_ax)
    ax.set_title(title)
    ax.set_xlabel(xlabel)
    ax.set_ylabel(ylabel)

    def update(frame):
        ax.clear()  # Clear the previous heatmap
        # Create the heatmap without recreating the color bar
        sns.heatmap(matrices[frame], annot=True, fmt=".2f", cmap='viridis', cbar=False, ax=ax)
        ax.set_title(title)
        ax.set_xlabel(xlabel)
        ax.set_ylabel(ylabel)

    anim = FuncAnimation(fig, update, frames=len(matrices), interval=interval, repeat=True)
    plt.close()  # Prevent it from showing a static plot
    return anim


In [60]:
relative_path = '../../data/namelist/ex_5.nml'
parameters = read_namelist(relative_path)

# Example usage
file_name = 'ex_5/T_out.csv'
temperature_matrix = read_and_reshape_temperature_csv(file_name, nx, ny)


#temperature_matrix = temperature_matrix[::100]  
temperature_matrix = temperature_matrix[:100, :, :]


temperature_matrix.shape



ValueError: Data size does not match expected dimensions.

In [58]:
# Generate the animation
anim = plot_heatmap_animation(temperature_matrix, title='Head diffusion delta peak', xlabel='Columns', ylabel='Rows')

# To display the animation in the notebook
HTML(anim.to_jshtml())

In [ ]:
# Example usage

matrix_delta = read_and_reshape_temperature_csv()
print("Reshaped Matrix:")
print(matrix_delta.shape)

matrix_delta = matrix_delta[:50,:,:]

